In [44]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.image as imread
import os
import seaborn as sns
import tensorflow
import keras
from keras.utils.vis_utils import plot_model
from tensorflow.keras import Input
from tensorflow.keras.layers import Conv2D, MaxPooling2D, Flatten, Dense, ZeroPadding2D, AveragePooling2D
from tensorflow.keras.models import Model

In [45]:
from tensorflow.keras.applications.resnet_v2 import ResNet50V2 as ResNet
from tensorflow.keras.applications.densenet import DenseNet121 as DenseNet
from tensorflow.keras.applications.inception_v3 import InceptionV3 as inceptionNet
from tensorflow.keras.applications.mobilenet_v2 import MobileNetV2 as MobileNet

In [72]:
def create_Model():
    input_ = Input(shape = (640,640,3))
    
    Res = ResNet(include_top=False, weights='imagenet', input_tensor=input_, pooling='average',classifier_activation='softmax')
    Inception = inceptionNet(include_top = False, weights = 'imagenet', input_tensor = input_, pooling = 'average', classifier_activation = 'softmax')
    
    Inception_mid_In = Inception.get_layer('mixed1').output
    Inception_mid_pad = ZeroPadding2D(padding = ((1,2),(2,1)))(Inception_mid_In)
    
    Res_mid_In = Res.get_layer('conv3_block1_out').output
    
    mid_concatenation = tensorflow.keras.layers.Concatenate(axis = -1)([Res_mid_In, Inception_mid_pad])
    mid_concatenation_conv2D1 = Conv2D(1024, (1,1), activation='relu', padding='same')(mid_concatenation)
    mid_concatenation_padding = ZeroPadding2D(padding = (0,0))(mid_concatenation_conv2D1)
    mid_concatenation_conv2D2 = Conv2D(3, (1,1), activation='relu', padding='same')(mid_concatenation_padding)
    
    
    MNet = MobileNet(include_top = False, weights = None, input_tensor = mid_concatenation_conv2D2, pooling = 'average', classifier_activation = 'softmax')
    MNet_Out_flatten = Flatten()(MNet.output)
    MNet_Out_Dense1 = Dense(256, activation = 'sigmoid')(MNet_Out_flatten)
    MNet_Out_Dense2 = Dense(64, activation = 'sigmoid')(MNet_Out_Dense1)

    Res_Out_flatten = Flatten()(Res.output)
    Res_Out_Dense1 = Dense(512, activation = 'sigmoid')(Res_Out_flatten)
    Res_Out_Dense2 = Dense(128, activation = 'sigmoid')(Res_Out_Dense1)
    Res_Out_Dense3 = Dense(64, activation = 'sigmoid')(Res_Out_Dense2)
    
    Inception_Out_flatten = Flatten()(Inception.output)
    Inception_Out_Dense1 = Dense(128, activation = 'sigmoid')(Inception_Out_flatten)
    Inception_Out_Dense2 = Dense(64, activation = 'sigmoid')(Inception_Out_Dense1)
    
    Res_Res_input = Res.get_layer('conv4_block3_out').output
    Res_Res_Conv1 = Conv2D(64, (2,2), activation='relu', padding='same')(Res_Res_input)
    Res_Res_Conv2 = Conv2D(8, (2,2), activation='relu', padding='same')(Res_Res_Conv1)
    Res_Res_flatten = Flatten()(Res_Res_Conv2)
    Res_Res_Dense1 = Dense(128, activation = 'sigmoid')(Res_Res_flatten)
    Res_Res_Dense2 = Dense(64, activation = 'sigmoid')(Res_Res_Dense1)
    
    Inception_Res_input = Inception.get_layer('mixed5').output
    Inception_Res_Conv1 = Conv2D(64, (2,2), activation='relu', padding='same')(Inception_Res_input)
    Inception_Res_Conv2 = Conv2D(8, (2,2), activation='relu', padding='same')(Inception_Res_Conv1)
    Inception_Res_flatten = Flatten()(Inception_Res_Conv2)
    Inception_Res_Dense1 = Dense(128, activation = 'sigmoid')(Inception_Res_flatten)
    Inception_Res_Dense2 = Dense(64, activation = 'sigmoid')(Inception_Res_Dense1)
    
    
    
    concatenation_out = tensorflow.keras.layers.Concatenate(axis = -1)([Res_Out_Dense3, Inception_Out_Dense2, MNet_Out_Dense2, Res_Res_Dense2, Inception_Res_Dense2])
    
    FStage_Dense1 = Dense(512, activation='sigmoid', name='FStage_Dense1')(concatenation_out)
    FStage_Dense2 = Dense(64, activation='sigmoid', name='FStage_Dense2')(FStage_Dense1)
    FStage_Dense3 = Dense(8, activation='sigmoid', name='FStage_Dense3')(FStage_Dense2)
    
    output_ = Dense(3, activation='sigmoid', name='output_')(FStage_Dense3)
    model = Model(input_, output_)
    
    model.compile(optimizer = 'adam', loss = 'categorical_crossentropy', metrics = ['accuracy'])
    return model


In [73]:
model = create_Model()
model.summary()
plot_model(model, show_shapes=True, show_layer_names=True)

Model: "model_19"
__________________________________________________________________________________________________
 Layer (type)                   Output Shape         Param #     Connected to                     
 input_32 (InputLayer)          [(None, 640, 640, 3  0           []                               
                                )]                                                                
                                                                                                  
 conv1_pad (ZeroPadding2D)      (None, 646, 646, 3)  0           ['input_32[0][0]']               
                                                                                                  
 conv1_conv (Conv2D)            (None, 320, 320, 64  9472        ['conv1_pad[0][0]']              
                                )                                                                 
                                                                                           

 batch_normalization_2916 (Batc  (None, 317, 317, 64  192        ['conv2d_2980[0][0]']            
 hNormalization)                )                                                                 
                                                                                                  
 conv2_block2_1_bn (BatchNormal  (None, 160, 160, 64  256        ['conv2_block2_1_conv[0][0]']    
 ization)                       )                                                                 
                                                                                                  
 activation_2916 (Activation)   (None, 317, 317, 64  0           ['batch_normalization_2916[0][0]'
                                )                                ]                                
                                                                                                  
 conv2_block2_1_relu (Activatio  (None, 160, 160, 64  0          ['conv2_block2_1_bn[0][0]']      
 n)       

                                                                                                  
 batch_normalization_2920 (Batc  (None, 77, 77, 48)  144         ['conv2d_2984[0][0]']            
 hNormalization)                                                                                  
                                                                                                  
 batch_normalization_2923 (Batc  (None, 77, 77, 96)  288         ['conv2d_2987[0][0]']            
 hNormalization)                                                                                  
                                                                                                  
 conv2_block3_2_conv (Conv2D)   (None, 80, 80, 64)   36864       ['conv2_block3_2_pad[0][0]']     
                                                                                                  
 activation_2920 (Activation)   (None, 77, 77, 48)   0           ['batch_normalization_2920[0][0]'
          

 activation_2929 (Activation)   (None, 77, 77, 64)   0           ['batch_normalization_2929[0][0]'
                                                                 ]                                
                                                                                                  
 conv3_block1_1_bn (BatchNormal  (None, 80, 80, 128)  512        ['conv3_block1_1_conv[0][0]']    
 ization)                                                                                         
                                                                                                  
 conv2d_2991 (Conv2D)           (None, 77, 77, 48)   12288       ['mixed0[0][0]']                 
                                                                                                  
 conv2d_2994 (Conv2D)           (None, 77, 77, 96)   55296       ['activation_2929[0][0]']        
                                                                                                  
 conv3_blo

                                                                                                  
 zero_padding2d_56 (ZeroPadding  (None, 80, 80, 288)  0          ['mixed1[0][0]']                 
 2D)                                                                                              
                                                                                                  
 concatenate_113 (Concatenate)  (None, 80, 80, 800)  0           ['conv3_block1_out[0][0]',       
                                                                  'zero_padding2d_56[0][0]']      
                                                                                                  
 conv2d_3072 (Conv2D)           (None, 80, 80, 1024  820224      ['concatenate_113[0][0]']        
                                )                                                                 
                                                                                                  
 zero_padd

...

 batch_normalization_2985 (Batc  (None, 18, 18, 320)  960        ['conv2d_3049[0][0]']            
 hNormalization)                                                                                  
                                                                                                  
 batch_normalization_2989 (Batc  (None, 18, 18, 192)  576        ['conv2d_3053[0][0]']            
 hNormalization)                                                                                  
                                                                                                  
 block_14_depthwise_BN (BatchNo  (None, 3, 3, 960)   3840        ['block_14_depthwise[0][0]']     
 rmalization)                                                                                     
                                                                                                  
 conv5_block2_preact_relu (Acti  (None, 20, 20, 2048  0          ['conv5_block2_preact_bn[0][0]'] 
 vation)  

 activation_2995 (Activation)   (None, 18, 18, 384)  0           ['batch_normalization_2995[0][0]'
                                                                 ]                                
                                                                                                  
 block_15_depthwise (DepthwiseC  (None, 3, 3, 960)   8640        ['block_15_expand_relu[0][0]']   
 onv2D)                                                                                           
                                                                                                  
 conv5_block2_3_conv (Conv2D)   (None, 20, 20, 2048  1050624     ['conv5_block2_2_relu[0][0]']    
                                )                                                                 
                                                                                                  
 conv2d_3056 (Conv2D)           (None, 18, 18, 384)  442368      ['activation_2991[0][0]']        
          

 alization)                                                                                       
                                                                                                  
 conv5_block3_1_conv (Conv2D)   (None, 20, 20, 512)  1048576     ['conv5_block3_preact_relu[0][0]'
                                                                 ]                                
                                                                                                  
 mixed9 (Concatenate)           (None, 18, 18, 2048  0           ['activation_2990[0][0]',        
                                )                                 'mixed9_0[0][0]',               
                                                                  'concatenate_111[0][0]',        
                                                                  'activation_2998[0][0]']        
                                                                                                  
 block_15_

 block_16_project (Conv2D)      (None, 3, 3, 320)    307200      ['block_16_depthwise_relu[0][0]']
                                                                                                  
 conv5_block3_out (Add)         (None, 20, 20, 2048  0           ['conv5_block2_out[0][0]',       
                                )                                 'conv5_block3_3_conv[0][0]']    
                                                                                                  
 conv2d_3063 (Conv2D)           (None, 18, 18, 320)  655360      ['mixed9[0][0]']                 
                                                                                                  
 batch_normalization_3001 (Batc  (None, 18, 18, 384)  1152       ['conv2d_3065[0][0]']            
 hNormalization)                                                                                  
                                                                                                  
 batch_nor

 flatten_77 (Flatten)           (None, 663552)       0           ['mixed10[0][0]']                
                                                                                                  
 flatten_75 (Flatten)           (None, 11520)        0           ['out_relu[0][0]']               
                                                                                                  
 flatten_78 (Flatten)           (None, 12800)        0           ['conv2d_3075[0][0]']            
                                                                                                  
 flatten_79 (Flatten)           (None, 11552)        0           ['conv2d_3077[0][0]']            
                                                                                                  
 dense_109 (Dense)              (None, 128)          65664       ['dense_108[0][0]']              
                                                                                                  
 dense_111